In [1]:
import os
import re
import json
import glob
import pandas as pd
from pandas import DataFrame, Series
import numpy as np
import networkx as nx
import seaborn as sns
import matplotlib.pyplot as plt

In [2]:
os.getcwd()

'/Users/limdongwoo/Downloads'

In [3]:
%cd '/Users/limdongwoo/jupyter'

/Users/limdongwoo/jupyter


In [5]:
!ls

[NEW] graph_JPKR.png


## json 日本

In [6]:
#%cd '/content/mydrive/My Drive/JpKorea'
import pandas as pd
b = pd.read_json("coronaJP.json")
b.shape

(60662254, 2)

In [18]:
b[:10]

screenname    retweet_sn
0           n4tm2   y___a__y___
1         kuri063     norinotes
2          hidyz1  ToruMasukawa
3      sakadamobo  taiju_okochi
4        seiimiya    tm_library
5       T23819027              
6  waverider_hide   pinwheel007
7         sg10214              
8           QmkDj    Kimuyuka15
9  nano_devices18

In [19]:
#b1 = b1.drop_duplicates(['screenname', 'retweet_sn'], keep='first')

In [20]:
#b1 = b.drop(['to_user_name', 'contents'], axis=1)
b1 = b
b1 = b1[b1.retweet_sn != '']
b1 = b1[b1.screenname != b1.retweet_sn]
b1 = b1.reset_index()
b1 = b1.drop('index',axis=1)
b1.shape

(44248733, 2)

In [21]:
b2 = b1.sample(n=50000)
b2 = b2.reset_index()
b2 = b2.drop('index', axis=1)
b2.shape

(50000, 2)

In [22]:
b2[:5]

screenname       retweet_sn
0     rissin_ben      combatmedic
1  LooP_guruguru      EARL_Med_Tw
2      FuyuOhagi        37bakutan
3      abubu0729  niigatacity_kib
4  kuripower2704       news_nakai

In [23]:
b2.retweet_sn.value_counts()

YahooNewsTopics    1452
livedoornews       1024
vG2AZlCr4F3hx6Y     442
nhk_news            422
dappi2019           401
                   ... 
bokeneko4             1
DUSToid_ama           1
gnpthnt311            1
nagamasa_san          1
nhk_chiba             1
Name: retweet_sn, Length: 12741, dtype: int64

In [24]:
len(b2[b2.screenname == b2.retweet_sn])

0

## RT GML Centrality

In [28]:
import networkx as nx
G = nx.Graph()
for i in range(len(b2)):
    G.add_edge(b2.screenname[i], b2.retweet_sn[i])
G.edges

EdgeView([('rissin_ben', 'combatmedic'), ('combatmedic', 'murabito823'), ('combatmedic', 'soundby_sho'), ('combatmedic', 'sorato_katsuki'), ('combatmedic', 'kanko_96mac'), ('combatmedic', 'qbkqbk'), ('combatmedic', 'afterschooloo12'), ('combatmedic', 'marishiokayama'), ('combatmedic', 'ozawanvoice'), ('combatmedic', 'kingdom'), ('combatmedic', 'tasks_s'), ('combatmedic', 'kawabikesento'), ('combatmedic', 'crazy_waterlily'), ('combatmedic', 'hiRoki_add9'), ('LooP_guruguru', 'EARL_Med_Tw'), ('EARL_Med_Tw', 'GintiyoSakura'), ('EARL_Med_Tw', 'Utapi69'), ('EARL_Med_Tw', 'tachibana_RR'), ('EARL_Med_Tw', 'mige_kae_ouji'), ('EARL_Med_Tw', 'titan3xFnfxte'), ('EARL_Med_Tw', 'kinoDC'), ('EARL_Med_Tw', 'meron3456'), ('EARL_Med_Tw', 'Andy_SV650S'), ('EARL_Med_Tw', 'errakiham'), ('EARL_Med_Tw', 'GunmaAfrica'), ('EARL_Med_Tw', 'takojuuu'), ('EARL_Med_Tw', 'yu012345yu'), ('EARL_Med_Tw', 'forzaoldbasterd'), ('EARL_Med_Tw', 'stuffaddiction'), ('EARL_Med_Tw', 'namaurako'), ('EARL_Med_Tw', 'mikage0903'), 

In [49]:
len(G)

55758

In [51]:
!pip install python-louvain

Processing /Users/limdongwoo/Library/Caches/pip/wheels/dd/6b/3b/87539deabac63a68ec34be2867308907d0544e11ba4d4e728d/python_louvain-0.13-py3-none-any.whl


In [53]:
import community
import networkx as nx
partition = community.best_partition(G)
nx.set_node_attributes(G, partition, 'community')
nx.write_gml(G, "200328_coronaJP.gml")

In [54]:
part = community.best_partition(G)
mod = community.modularity(part,G)
mod

0.9423697160200256

### community sorted list

In [55]:
!ls

200328_coronaJP.gml coronaJP.json


In [56]:
H = nx.read_gml('200328_coronaJP.gml')
len(H)

55758

In [57]:
comm99=nx.get_node_attributes(H,'community')
commlist99 = sorted(comm99.items(), key=lambda x: x[1], reverse=False)
df99 = DataFrame(commlist99)
df99.columns = ['sn', 'community99']
df99

sn  community99
0           rissin_ben            0
1          combatmedic            0
2         livehonestly            0
3        SekoHiroshige            0
4      niwanihaeteruki            0
...                ...          ...
55753        kogitaro_         8746
55754  shintarokurachi         8747
55755       bindeballe         8747
55756   sukhumvitanode         8748
55757   MysteriousSurv         8748

[55758 rows x 2 columns]

In [58]:
dflen99 = df99['community99'].value_counts()
dflen99[:30]

9      1352
16     1114
19     1067
63      971
13      897
42      833
37      673
1       648
10      635
58      627
14      623
69      604
18      574
61      508
38      472
45      463
36      462
12      457
62      451
141     400
44      383
101     373
29      357
120     342
107     337
56      333
26      323
35      322
103     321
90      315
Name: community99, dtype: int64

In [59]:
b3 = b2.retweet_sn.value_counts()
b3[:20]

YahooNewsTopics    1452
livedoornews       1024
vG2AZlCr4F3hx6Y     442
nhk_news            422
dappi2019           401
Sankei_news         389
konotarogomame      380
Narodovlastiye      354
katsuyatakasu       346
EARL_Med_Tw         314
UN_NERV             242
sonkoubun           237
nhk_seikatsu        224
K_Onishi            184
jijicom             177
sharenewsjapan1     175
knife9000           171
Ortho_FL            162
tbs_news            160
SatoMasahisa        159
Name: retweet_sn, dtype: int64

In [0]:
## August

#保守 
jda1BekUDve1ccx    
Sankei_news        
KadotaRyusho  
anonymous201504     
RibbonChieko
daitojimari
SatoMasahisa 
vG2AZlCr4F3hx6Y  
dappi2019 
hyakutanaoki
hoshusokuhou 
katsuyatakasu  
yoshidakoichiro
smith796000 




#liberal
umetaro_uy  
wanpakuten 
kikko_no_blog  
nogutiya 





    
       
     
    
     
         
       
        
           
    
    
       
                   

# jiken
miyurindarukoro
# aimai
mi2_yes 

In [0]:
## October

#保守 
dappi2019
vG2AZlCr4F3hx6Y
jda1BekUDve1ccx    
KadotaRyusho
takenoma 
Sankei_news
RibbonChieko 
sharenewsjapan1
shounantk 
yoshidakoichiro   


#liberal
Narodovlastiye 
wanpakuten    
kikko_no_blog
masaru_kaneko
aiko33151709
yumidesu_4649     
Dgoutokuji 
bSM2TC2coIKWrlM       
knife9000        
meow164            
   
       
  
        
        
      
        
           
   
          
         
          
            
       
  
     

In [0]:
##November

#保守 
35 dappi2019   
16 vG2AZlCr4F3hx6Y
11 jda1BekUDve1ccx  
12 KadotaRyusho  
29 Sankei_news
20 RibbonChieko 
4  takenoma
30 shounantk 

#liberal
23 wanpakuten    
9  Narodovlastiye       
19 kikko_no_blog 
14 aiko33151709  
7  masaru_kaneko
0  yumidesu_4649
18 Dgoutokuji    
15 knife9000
33 bSM2TC2coIKWrlM
2  meow164
3  umetaro_uy 

#曖昧         
ohIl7blO0mwjp33 

In [0]:
##December

#保守 
YOSHISHIGEKAGO1
KadotaRyusho    
sharenewsjapan1    
vG2AZlCr4F3hx6Y   

#liberal
Narodovlastiye 
kikko_no_blog    
wanpakuten   
nogutiya   
aiko33151709     
brahmslover  
yumidesu_4649 
masaru_kaneko  
knife9000      
toubennbenn      
bSM2TC2coIKWrlM 
Dgoutokuji      
product1954 
litera_web    
SamejimaH   
kemuchiman 

In [0]:
## July
###前回###

#保守 
anonymous201504
KadotaRyusho
SekoHiroshige
daitojimari
dappi2019
Sankei_news
jda1BekUDve1ccx
katsuyatakasu
sharenewsjapan
RibbonChieko

#liberal
kikko_no_blog
Beriozka1917
brahmslover
aiko33151709
yumidesu_4649
knife9000
wanpakuten
tekina_osamu
toubennbenn
masaru_kaneko

In [0]:
df99[df99['sn'] == 'Sankei_news']

sn  community99
7426  Sankei_news           10

In [0]:
df99[df99['sn'] == 'KadotaRyusho']

sn  community99
14592  KadotaRyusho           18

In [0]:
df99[df99['sn'] == 'anonymous201504']

sn  community99
3030  anonymous201504            4

In [0]:
df99[df99['sn'] == 'RibbonChieko']

sn  community99
19959  RibbonChieko           31

In [0]:
df99[df99['sn'] == 'daitojimari']

sn  community99
11919  daitojimari           15

In [0]:
df99[df99['sn'] == 'SatoMasahisa']

sn  community99
18032  SatoMasahisa           26

In [0]:
df99[df99['sn'] == 'vG2AZlCr4F3hx6Y']

sn  community99
1079  vG2AZlCr4F3hx6Y            2

In [0]:
df99[df99['sn'] == 'dappi2019']

sn  community99
14599  dappi2019           18

In [0]:
df99[df99['sn'] == 'hyakutanaoki']

sn  community99
18756  hyakutanaoki           27

In [0]:
df99[df99['sn'] == 'hoshusokuhou']

sn  community99
21082  hoshusokuhou           33

In [0]:
df99[df99['sn'] == 'katsuyatakasu']

sn  community99
23866  katsuyatakasu           39

In [0]:
df99[df99['sn'] == 'yoshidakoichiro']

sn  community99
28025  yoshidakoichiro           53

In [0]:
df99[df99['sn'] == 'smith796000']

sn  community99
4162  smith796000            6

In [0]:
df99[df99['sn'] == 'umetaro_uy']

sn  community99
9519  umetaro_uy           12

In [0]:
df99[df99['sn'] == 'wanpakuten']

sn  community99
5774  wanpakuten            8

In [0]:
df99[df99['sn'] == 'kikko_no_blog']

sn  community99
12627  kikko_no_blog           16

In [0]:
df99[df99['sn'] == 'nogutiya']

sn  community99
13434  nogutiya           17

In [0]:
dflen99 = df99['community99'].value_counts()
dflen99[:40]

4     4381
1     1658
5     1406
25    1251
18    1213
14    1095
13    1066
32     888
22     841
26     834
3      746
17     637
8      632
20     629
0      612
21     564
24     540
28     539
11     538
33     527
7      491
35     444
9      437
54     409
10     401
39     375
40     350
30     339
37     339
23     334
59     325
95     324
49     317
43     294
38     290
31     253
6      251
75     210
44     163
77     156
Name: community99, dtype: int64

In [0]:
community99 = df99[df99['community99'].isin(['0'])]
community99[:5]

sn  community99
0          244yura            0
1  M8UGD3eAnhiGCWy            0
2         takenoma            0
3      Haseani1981            0
4       Sayonara_K            0

In [0]:
dflen1 = df['community'].value_counts()
dflen1[:20]

19    2503
3     1670
10    1390
25    1307
18    1236
9     1156
2     1095
41    1012
15    1005
40     931
5      930
36     868
27     867
22     799
28     758
24     753
0      737
44     697
49     668
21     607
Name: community, dtype: int64

In [0]:
dflen = df['community'].value_counts()
dflen[:20]

19    2503
3     1670
10    1390
25    1307
18    1236
9     1156
2     1095
41    1012
15    1005
40     931
5      930
36     868
27     867
22     799
28     758
24     753
0      737
44     697
49     668
21     607
Name: community, dtype: int64

In [0]:
#community = df[df['community'].isin(['0', '1', '2'])]
community = df[df['community'].isin(['17'])]
community

sn  community
10840     purimura4458         17
10841  Futokaikosaiban         17
10842      beni_bara29         17
10843  demauyo_tadaimo         17
10844           aznote         17
...                ...        ...
11378  OwucJVDxppuRUw9         17
11379        clearNica         17
11380     ryoh12240511         17
11381  TakayoshiIsoza1         17
11382        chonozero         17

[543 rows x 2 columns]

### degree & between centrality

In [0]:
dc = nx.degree_centrality(G)
dc.items()

dict_items([('244yura', 5.2659294365455505e-05), ('nondakure56', 0.0006845708267509215), ('gkmond', 5.2659294365455505e-05), ('blueash009', 0.001158504476040021), ('kikyoya_rinbe', 2.6329647182727753e-05), ('kotarotatsumi', 0.0005265929436545551), ('2YzWL1afCK51nLy', 5.2659294365455505e-05), ('jda1BekUDve1ccx', 0.013059505002632966), ('Japan_maiko', 0.00013164823591363877), ('Moeyo2013', 2.6329647182727753e-05), ('watarloo', 2.6329647182727753e-05), ('hinakoozaki', 2.6329647182727753e-05), ('makopons5', 2.6329647182727753e-05), ('today_gochisou', 5.2659294365455505e-05), ('torisaka', 0.00018430753027909427), ('yumidesu_4649', 0.011927330173775673), ('_meesk', 0.00010531858873091101), ('murakamisatoko', 0.00047393364928909954), ('hikarinotaki', 2.6329647182727753e-05), ('okabaeri9111', 0.00036861506055818854), ('karyou_luna', 2.6329647182727753e-05), ('cna_urei', 0.001922064244339126), ('newscolle2017', 0.00010531858873091101), ('akasakaromantei', 0.004555028962611901), ('yz_moon_sait',

In [0]:
dc_list = sorted(dc.items(), key=lambda x: x[1], reverse=True)
dc_list[:20]

[('anonymous201504', 0.035650342285413375),
 ('kikko_no_blog', 0.034939441811479725),
 ('KadotaRyusho', 0.027145866245392312),
 ('SekoHiroshige', 0.021379673512374936),
 ('daitojimari', 0.019615587151132177),
 ('dappi2019', 0.016456029489204844),
 ('Beriozka1917', 0.016034755134281202),
 ('Sankei_news', 0.015297525013164824),
 ('brahmslover', 0.01358609794628752),
 ('aiko33151709', 0.013112164296998421),
 ('jda1BekUDve1ccx', 0.013059505002632966),
 ('yumidesu_4649', 0.011927330173775673),
 ('knife9000', 0.011743022643496578),
 ('wanpakuten', 0.010953133228014745),
 ('katsuyatakasu', 0.010716166403370196),
 ('tekina_osamu', 0.010215903106898369),
 ('sharenewsjapan', 0.010057925223802002),
 ('toubennbenn', 0.00903106898367562),
 ('masaru_kaneko', 0.008846761453396525),
 ('RibbonChieko', 0.007846234860452871)]

In [0]:
dc1 = nx.degree_centrality(G)
dc1.items()

dict_items([('yukadayo0307', 1.993660160689009e-05), ('raichan_owo', 1.993660160689009e-05), ('kirin_chan3', 1.993660160689009e-05), ('livedoornews', 0.0006379712514204828), ('comaro_ak', 7.974640642756035e-05), ('tougamo4041', 0.00011961960964134054), ('foodlike99', 7.974640642756035e-05), ('u8aMrilT2oAho', 3.987320321378018e-05), ('tononotomokun', 1.993660160689009e-05), ('hatoyamayukio', 0.0009768934787376144), ('takapee99', 3.987320321378018e-05), ('OA5KVuDedw1E8b1', 1.993660160689009e-05), ('IYbY5A3yYWOUQH5', 3.987320321378018e-05), ('nikejapan', 1.993660160689009e-05), ('ZhhW4uRZsykc9T7', 5.980980482067027e-05), ('osakadaisuki22', 1.993660160689009e-05), ('a_42d8', 1.993660160689009e-05), ('dzljjtp3KCQiOmr', 1.993660160689009e-05), ('y_RiCh24', 1.993660160689009e-05), ('peony_44', 1.993660160689009e-05), ('Abeisover', 5.980980482067027e-05), ('PistonMach', 1.993660160689009e-05), ('padyoumk', 1.993660160689009e-05), ('stop_abe_seiji', 0.001375625510875416), ('hinomarujkrei', 1.99

In [0]:
dc_list1 = sorted(dc1.items(), key=lambda x: x[1], reverse=True)
dc_list1[:20]

[('anonymous201504', 0.021172670906517276),
 ('sharenewsjapan', 0.013237903466975018),
 ('Sankei_news', 0.010765764867720648),
 ('nhk_news', 0.008114196854004265),
 ('daitojimari', 0.007934767439542256),
 ('katsuyatakasu', 0.007296796188121772),
 ('KadotaRyusho', 0.007097430172052871),
 ('YahooNewsTopics', 0.006339839310991048),
 ('AbeShinzo', 0.005821487669211906),
 ('hoshusokuhou', 0.005482565441894774),
 ('SekoHiroshige', 0.00458541836958472),
 ('brahmslover', 0.004007256922984908),
 ('murrhauser', 0.0038477641101297873),
 ('hyakutanaoki', 0.003827827508522897),
 ('takenoma', 0.0037281445004884463),
 ('mizukikenkan', 0.0035088418828126554),
 ('shiikazuo', 0.0033094758667437545),
 ('SatoMasahisa', 0.0032696026635299744),
 ('kikko_no_blog', 0.0031101098506748537),
 ('knife9000', 0.002990490241033513)]

In [0]:
dcb = nx.degree_centrality(G)
dcb.items()

dict_items([(' DivaSoul3', 0.000132013201320132), (' narendramodi', 0.0006600660066006601), (' shelly9812', 2.6402640264026404e-05), (' 1127_VANILLA', 0.000976897689768977), (' hQetP75Gn74tt0G', 7.920792079207921e-05), (' sydbris', 0.007498349834983499), (' sisichulchul', 0.00047524752475247524), (' JiyeonIhn', 5.280528052805281e-05), (' xu4NyBAqgz6ZQWd', 0.00031683168316831684), (' goto7799', 0.0017161716171617163), (' jrleem', 0.00023762376237623762), (' moonlover333', 0.011590759075907592), (' Eunwol100', 2.6402640264026404e-05), (' karljung2085', 0.0018745874587458747), (' radiokjh', 7.920792079207921e-05), (' gargyKoo', 0.004198019801980198), (' porori033', 5.280528052805281e-05), (' gobackhome11', 0.001636963696369637), (' zumacher', 0.00023762376237623762), (' rokmc913j', 0.0013993399339933994), (' tdidyxkgxktd', 7.920792079207921e-05), (' 8tvmMsF9wJ7uKpM', 0.001188118811881188), (' wJvH9bijHtqxPkA', 5.280528052805281e-05), (' Heuk_SUGA_0309', 5.280528052805281e-05), (' mamamooX

In [0]:
dcb_list1 = sorted(dcb.items(), key=lambda x: x[1], reverse=True)
dcb_list1[:20]

[(' TheBlueHouseKR', 0.02621782178217822),
 (' TXT_members', 0.02114851485148515),
 (' happy_CSR', 0.01343894389438944),
 (' moonlover333', 0.011590759075907592),
 (' park_pyung', 0.011537953795379538),
 (' ting1574', 0.008501650165016502),
 (' usminjooforum', 0.008211221122112212),
 (' DrPyo', 0.008026402640264026),
 (' weareoneEXO', 0.007841584158415842),
 (' dak_dak_dak', 0.007815181518151816),
 (' binmudum', 0.007656765676567657),
 (' sydbris', 0.007498349834983499),
 (' pyeonjeon', 0.00704950495049505),
 (' mettayoon', 0.0066270627062706275),
 (' dytpqdlxn', 0.006415841584158416),
 (' A4uaMRkKSYeixW4', 0.00638943894389439),
 (' go1rani', 0.006231023102310231),
 (' Schalom1004', 0.006151815181518152),
 (' histopian', 0.005887788778877888),
 (' pinkcloudaway_', 0.005570957095709571)]

In [0]:
dcb2 = nx.degree_centrality(G)
dcb2.items()

dict_items([('ChyarcoV', 7.828248233751492e-05), ('Mumble_D_', 1.957062058437873e-05), ('dakeabc', 3.914124116875746e-05), ('lkjhkiyy8774787', 0.0001369943440906511), ('icebear0005', 9.785310292189365e-05), ('inugami231', 1.957062058437873e-05), ('ysong030623', 3.914124116875746e-05), ('canayoung_C', 3.914124116875746e-05), ('elshu_su', 3.914124116875746e-05), ('milky_SU_', 1.957062058437873e-05), ('o0O00O00oOooo0', 1.957062058437873e-05), ('ggoul_ddeok', 1.957062058437873e-05), ('ey198', 1.957062058437873e-05), ('Kiso_Korean_bot', 9.785310292189365e-05), ('kimhi__28', 1.957062058437873e-05), ('izone_koitomi', 3.914124116875746e-05), ('bopyeontadang', 1.957062058437873e-05), ('05m57hoqZN3MFGv', 1.957062058437873e-05), ('Bob_9n', 0.00017613558525940857), ('oh_hjsss1232', 1.957062058437873e-05), ('Eugeniasarahlee', 1.957062058437873e-05), ('soundly_s', 0.0001369943440906511), ('CatsCradle735', 0.0001369943440906511), ('c2bwsjuhmEW3tbX', 0.00023484744701254476), ('llomunim_', 3.9141241168

In [0]:
dcb2_list1 = sorted(dcb2.items(), key=lambda x: x[1], reverse=True)
dcb2_list1[:20]

[('moonriver365', 0.0061647454840793),
 ('Schalom1004', 0.004070689081550775),
 ('BigHitEnt', 0.003620564808110065),
 ('BTS_twt', 0.0033074348787600055),
 ('4545ikuaaa', 0.0029943049494099458),
 ('newsvop', 0.0029943049494099458),
 ('DrPyo', 0.002916022467072431),
 ('TheBlueHouseKR', 0.0026420337788911285),
 ('hankyungmedia', 0.0026028925377223713),
 ('moonlover333', 0.002544180675969235),
 ('cha_young', 0.0021331976436972815),
 ('usminjooforum', 0.002015773920191009),
 ('bts_bighit', 0.001976632679022252),
 ('pbjs9876', 0.001957062058437873),
 ('leejongsul78', 0.0019179208172691155),
 ('JTBC_news', 0.0019179208172691155),
 ('joongangilbo', 0.0017809264731784645),
 ('yonhaptweet', 0.0016439321290878132),
 ('patriamea', 0.0016243615085034346),
 ('shinfran', 0.0016047908879190558)]

In [0]:
len(G)

37981

In [0]:
import progressbar
from time import sleep
bar = progressbar.ProgressBar(maxval=20, \
    widgets=[progressbar.Bar('=', '[', ']'), ' ', progressbar.Percentage()])
bar.start()
bet = nx.betweenness_centrality(G, weight=None)
bar.finish()

[========================================================================] 100%


In [0]:
type(bet)

dict

In [0]:
betcen = sorted(bet.items(), key=lambda x: x[1], reverse=True)
betcen[:20]

[('kikko_no_blog', 0.1072830171495343),
 ('anonymous201504', 0.09397322824178855),
 ('Sankei_news', 0.06698008376357419),
 ('KadotaRyusho', 0.04865347369342787),
 ('daitojimari', 0.0380169454355295),
 ('SekoHiroshige', 0.03727120705399018),
 ('Beriozka1917', 0.03432417315279846),
 ('sharenewsjapan', 0.03420056810623573),
 ('jda1BekUDve1ccx', 0.033486788167495236),
 ('brahmslover', 0.03188222793670413),
 ('dappi2019', 0.028857879927008008),
 ('60z', 0.028759678929837208),
 ('wanpakuten', 0.02651762261510276),
 ('katsuyatakasu', 0.026221435783565526),
 ('shiikazuo', 0.025041201122653053),
 ('knife9000', 0.024998947416699734),
 ('tekina_osamu', 0.023378997353941545),
 ('aiko33151709', 0.022755470375150414),
 ('yumidesu_4649', 0.020222903205536342),
 ('ppsh41_1945', 0.016338725599726232)]

In [0]:
len(bet1)

50160

In [0]:
import progressbar
from time import sleep
bar = progressbar.ProgressBar(maxval=20, \
    widgets=[progressbar.Bar('=', '[', ']'), ' ', progressbar.Percentage()])
bar.start()
bet1 = nx.betweenness_centrality(G, weight=None)
bar.finish()

[========================================================================] 100%


In [0]:
betcen1 = sorted(bet1.items(), key=lambda x: x[1], reverse=True)
betcen1[:20]

[('anonymous201504', 0.026971172895799776),
 ('sharenewsjapan', 0.01583136878083036),
 ('Sankei_news', 0.012308135644390103),
 ('nhk_news', 0.008777903925132792),
 ('daitojimari', 0.008355141847964037),
 ('AbeShinzo', 0.007384679708497453),
 ('KadotaRyusho', 0.0069466881876506115),
 ('katsuyatakasu', 0.0062927285696789195),
 ('brahmslover', 0.006204314532628005),
 ('YahooNewsTopics', 0.0061234594759065585),
 ('hoshusokuhou', 0.004780424783579457),
 ('shiikazuo', 0.004569242757739257),
 ('knife9000', 0.004477944081350524),
 ('SekoHiroshige', 0.004274332030792524),
 ('hyakutanaoki', 0.0038892669530134053),
 ('kikko_no_blog', 0.0037080368312576327),
 ('murrhauser', 0.003573985548123429),
 ('ISOKO_MOCHIZUKI', 0.0032232051491225327),
 ('SatoMasahisa', 0.003142539207354916),
 ('YuzukiMuroi', 0.002961611181882274)]

In [0]:
import progressbar
from time import sleep
bar = progressbar.ProgressBar(maxval=20, \
    widgets=[progressbar.Bar('=', '[', ']'), ' ', progressbar.Percentage()])
bar.start()
bet2 = nx.betweenness_centrality(G, weight=None)
bar.finish()

[========================================================================] 100%


In [0]:
betcen2 = sorted(bet2.items(), key=lambda x: x[1], reverse=True)
betcen2[:20]

[(' TheBlueHouseKR', 0.07183151152850925),
 (' go1rani', 0.05171487626021153),
 (' BTS_twt', 0.04162071346312237),
 (' TXT_members', 0.03695730728482892),
 (' armywlov13', 0.036332852147759005),
 (' pyeonjeon', 0.03559477709786843),
 (' A4uaMRkKSYeixW4', 0.033338486732011924),
 (' laVnwl8oa4HU8M6', 0.025821302698360957),
 (' bullet_proofly', 0.02580974628376057),
 (' sydbris', 0.02510128268429277),
 (' moonlover333', 0.025083238322663397),
 (' born_aRMy_', 0.024033399070909227),
 (' ting1574', 0.022298736552581883),
 (' fuckyou_1248', 0.02181029095926957),
 (' happy_CSR', 0.021764454090018266),
 (' park_pyung', 0.021294532028180983),
 (' yonhaptweet', 0.01932687775389856),
 (' weareoneEXO', 0.01897925828049776),
 (' ARMY46940311', 0.015865767841109386),
 (' pinkcloudaway_', 0.01397704111374051)]

In [0]:
import progressbar
from time import sleep
bar = progressbar.ProgressBar(maxval=20, \
    widgets=[progressbar.Bar('=', '[', ']'), ' ', progressbar.Percentage()])
bar.start()
bet3 = nx.betweenness_centrality(G, weight=None)
bar.finish()

[========================================================================] 100%


In [0]:
betcen3 = sorted(bet3.items(), key=lambda x: x[1], reverse=True)
betcen3[:20]

[('moonriver365', 0.006847016606559585),
 ('BigHitEnt', 0.005328319702515404),
 ('KarasumaGojo', 0.005130586842155532),
 ('starboy_68', 0.0049304328478615225),
 ('_aesae', 0.004798831378708793),
 ('koreanpowergood', 0.004725064797985491),
 ('8cac891602cb491', 0.004687959538632072),
 ('havemomufullday', 0.004653714782776269),
 ('It_Looks_Bleak', 0.004647499954030338),
 ('Lrlouren', 0.004602193676284819),
 ('neiluniverse', 0.004474546982086568),
 ('BTS_twt', 0.004312460233437434),
 ('Natsunokori', 0.004016179912969008),
 ('vQQLG3GUAJZ5FMi', 0.003739250494732735),
 ('Serahwang2017', 0.0037122221989932497),
 ('eunju105', 0.0033922635586742995),
 ('yoshikin_kr', 0.003206568331620687),
 ('Schalom1004', 0.003052365602566647),
 ('mattymatty_', 0.0029803904638989525),
 ('Fun_To_PLAY_eve', 0.002831106646423489)]